In [99]:
import simpy
import random
import matplotlib.pyplot as plt
from scipy import stats 

tiempo={}
nMaquina=[0,0]
vehiculosPesados=['buseta','bus','camion']
repetir=[]
aprobados=[]
no_aprobados=[]
num_vehiculos_por_dia=[]
carril1=[]
carril2=[]
carril3=[]

carriles={'carril1':[],'carril2':[],'carril3':[]}

class EMOV(object):
    
    def __init__(self, environment, num_carril_normal, num_carril_grande):
        self.env=environment
        self.carril_normal = simpy.Resource(environment, num_carril_normal)
        self.carril_grande = simpy.Resource(environment, num_carril_grande)

    def revisión(self, vehiculo):

        mu, sigma = 20/60, 10/60 # media y desvio estandar
        normal = stats.norm(mu, sigma)
        tiempoAleatorio = abs(normal.rvs(1)) # genera aleatorios

        print('El vehiculo: ',vehiculo,)

        yield self.env.timeout(tiempoAleatorio)
        

        
    
def llegada_vehiculo(env, nombre, emov):

    global nMaquina
    global repetir
    global aprobados
    global no_aprobados
    global carril1
    global carril2
    global carril3

    print('Llega vehiculo: %s a la hora %.2f.' % (nombre, env.now))
    
    vehi=nombre.split(' ')[0]

    t=random.randrange(3,5)/60

    yield env.timeout(t)

    print('El vehiculo ',nombre,' se estaciono hasta la hora',env.now)

    t=random.randrange(1,3)/60

    yield env.timeout(t)

    print('El vehiculo ',nombre,' saco el turno a la hora',env.now)

    t=random.randrange(5,10)/60

    yield env.timeout(t)

    print('El vehiculo ',nombre,' termino de pagar la matricula a la hora',env.now)

    if vehi not in vehiculosPesados:

        with emov.carril_normal.request() as carril_norm:

            yield carril_norm
            nM=0
            for i in range(len(nMaquina)):
                if nMaquina[i] == 0:
                    nM=i+1
                    nMaquina[i] = str(carril_norm)
                    break

            vehiculo=nombre.split(' ')[0]

            if nM == 1:
                carril1.append(1)
            else:
                carril2.append(1)
            
            print('El vehiculo ',nombre,' entra a la revision en el carril:',nM,' a la hora',env.now)

            yield env.process(emov.revisión(nombre))
            nMaquina[nM-1]=0
            print('Vehiculo [%s] revisado a las %.2f.' % (nombre, env.now))

            pasa_no_pasa = [0,1] 
            pasa_no_pasa=random.choices(pasa_no_pasa, weights=(40,60), k=1)

            if pasa_no_pasa == 1:
                aprobados.append(1)
                t=random.randrange(1,3)/60
                yield env.timeout(t)
                print('Vehiculo [%s] puesto el sello a las %.2f.' % (nombre, env.now))
            else:
                no_aprobados.append(1)
                repetir.append(nombre)
            
            t=random.randrange(5,10)/60
            yield env.timeout(t)
            print('Vehiculo [%s] sale a las %.2f.' % (nombre, env.now))
            
            # k=env.now 
            # if k in tiempo:
            #     tiempo[k]=tiempo[k]+1
            # else:
            #     tiempo[k]=1

    else:

        with emov.carril_grande.request() as carril_grande:

            yield carril_grande
            
            print('El vehiculo ',nombre,' entra a la revision en el carril:',3,' a la hora',env.now)

            yield env.process(emov.revisión(nombre))
            print('Vehiculo [%s] revisado a las %.2f.' % (nombre, env.now))
            carril3.append(1)
            pasa_no_pasa = [0,1] 
            pasa_no_pasa=random.choices(pasa_no_pasa, weights=(40,60), k=1)

            if pasa_no_pasa == 1:
                aprobados.append(1)
                t=random.randrange(1,3)/60
                yield env.timeout(t)
                print('Vehiculo [%s] puesto el sello a las %.2f.' % (nombre, env.now))
            else:
                no_aprobados.append(1)
                repetir.append(nombre)

            t=random.randrange(5,10)/60
            yield env.timeout(t)
            print('Vehiculo [%s] sale a las %.2f.' % (nombre, env.now))
            


def ejecutar_simulacion(env, num_carril_normal, num_carril_grande):
    global num_vehiculos_por_dia
    global carril1
    global carril2
    global carril3
    global carriles
    emov=EMOV(env, num_carril_normal, num_carril_grande)
    v={'buseta':0,'bus':0,'camion':0,'automovil':0}
    # Ejecutamos la simulacion
    acum=0
    acum1=0
    while True:
        # yield env.timeout(random.randint(intervalo-3, intervalo+3))
        yield env.timeout(3/60)
        # Mientras se lavan los vehiculos generamos mas vehiculos
        vehiculos = ['buseta','bus','camion','automovil'] 
        vehiculo=random.choices(vehiculos, weights=(15,15,15,85), k=1)
        v[str(vehiculo[0])]+=1

        acum+=round(env.now)
        acum1+=1



        if acum%24 == 0:
            carriles['carril1'].append(len(carril1))
            carriles['carril2'].append(len(carril2))
            carriles['carril3'].append(len(carril3))
            num_vehiculos_por_dia.append(acum1)
            acum1=0
            acum=0
            carril1=[]
            carril2=[]
            carril3=[]

        env.process(llegada_vehiculo(env, str(str(vehiculo[0])+' '+str(v[str(vehiculo[0])])),emov))

In [100]:
NUM_CARRIL_NORMAL = 2

NUM_CARRIL_GRANDE = 1

TIEMPO_SIMULACION = 30*24


print('Lavanderia UPS')
# Inicializamos la semilla aleatoria
random.seed(77)

# Creamos el entorno de simulacion
env=simpy.Environment()
env.process(ejecutar_simulacion(env, NUM_CARRIL_NORMAL, NUM_CARRIL_GRANDE))

# Ejecutamos el proceso durante el tiempo de simulacion
env.run(until = TIEMPO_SIMULACION)

# print(tiempo)
# # Generamos una grafica en base al diccionario del tiempo
# etiqueta = list(tiempo.keys())
# valores = list(tiempo.values())
# plt.bar(range(len(tiempo)), valores, align="center", tick_label=etiqueta)
# plt.title("Tiempo/Salida Vehiculos")
# plt.xlabel("Tiempo")
# plt.ylabel("Nro. Vehiculos")
# plt.show()

Lavanderia UPS
Llega vehiculo: automovil 1 a la hora 0.05.
Llega vehiculo: bus 1 a la hora 0.10.
El vehiculo  automovil 1  se estaciono hasta la hora 0.11666666666666667
El vehiculo  automovil 1  saco el turno a la hora 0.13333333333333333
Llega vehiculo: automovil 2 a la hora 0.15.
El vehiculo  bus 1  se estaciono hasta la hora 0.15000000000000002
El vehiculo  bus 1  saco el turno a la hora 0.16666666666666669
Llega vehiculo: automovil 3 a la hora 0.20.
El vehiculo  automovil 2  se estaciono hasta la hora 0.2
El vehiculo  automovil 2  saco el turno a la hora 0.23333333333333334
El vehiculo  automovil 1  termino de pagar la matricula a la hora 0.25
Llega vehiculo: automovil 4 a la hora 0.25.
El vehiculo  automovil 3  se estaciono hasta la hora 0.25
El vehiculo  automovil 1  entra a la revision en el carril: 1  a la hora 0.25
El vehiculo:  automovil 1
El vehiculo  automovil 3  saco el turno a la hora 0.26666666666666666
Llega vehiculo: automovil 5 a la hora 0.30.
El vehiculo  bus 1  ter

In [101]:
# etiqueta = list(range(len(num_vehiculos_por_dia)))
# valores = num_vehiculos_por_dia
# plt.bar(etiqueta, valores, align="center", tick_label=etiqueta)
# plt.title("Tiempo/Salida Vehiculos")
# plt.xlabel("Tiempo")
# plt.ylabel("Nro. Vehiculos")
# plt.show()
print(len(num_vehiculos_por_dia))
print(num_vehiculos_por_dia[0])

403
1
